In [8]:
# Re-import required packages after kernel reset
import json
import pandas as pd
import geopandas as gpd
import folium
from folium import Choropleth
from shapely.geometry import Point, shape
from shapely.strtree import STRtree

# Reload raw GeoJSON and CSV files
geojson_path = "/users/mobi/downloads/Police_Precincts.geojson"
csv_path = "/users/mobi/downloads/Baltimore-county-crime-analysis/data/Public_Crime_Data.csv"

with open(geojson_path, "r") as f:
    raw_geojson = json.load(f)

crime_df = pd.read_csv(csv_path)

# Prepare precinct geometries and properties
precinct_geometries = [shape(f["geometry"]) for f in raw_geojson["features"]]
precinct_properties = [f["properties"] for f in raw_geojson["features"]]

# Sample and convert crime data to points
crime_sample = crime_df.dropna(subset=["OBF_YCOORD", "OBF_XCOORD"]).sample(n=10000, random_state=42)
crime_points = [Point(xy) for xy in zip(crime_sample["OBF_XCOORD"], crime_sample["OBF_YCOORD"])]

# Build STRtree for spatial queries
tree = STRtree(precinct_geometries)
polygon_id_to_name = {id(polygon): props["NAME"] for polygon, props in zip(precinct_geometries, precinct_properties)}
crime_counts = {name: 0 for name in polygon_id_to_name.values()}

# Spatial match
for pt in crime_points:
    for poly_idx in tree.query(pt):
        poly = precinct_geometries[poly_idx]  # ✅ direct from list
        if poly.contains(pt):
            name = polygon_id_to_name[id(poly)]
            crime_counts[name] += 1

            break

# Inject counts into raw GeoJSON
for feature in raw_geojson["features"]:
    name = feature["properties"].get("NAME")
    feature["properties"]["crime_count"] = crime_counts.get(name, 0)

# Save GeoJSON with crime counts
choropleth_geojson_path = "/users/mobi/downloads/baltimore-county-crime-analysis/outputs/baltimore_precincts_choropleth_counts.geojson"
with open(choropleth_geojson_path, "w") as f:
    json.dump(raw_geojson, f)

choropleth_geojson_path  # Return path first before regenerating map


/var/folders/b9/t16cvz9j5plbst_c7jrxgxl40000gn/T/ipykernel_74874/3625825790.py:17: DtypeWarning: Columns (9) have mixed types. Specify dtype option on import or set low_memory=False.
  crime_df = pd.read_csv(csv_path)


'/users/mobi/downloads/baltimore-county-crime-analysis/outputs/baltimore_precincts_choropleth_counts.geojson'

In [12]:
# Rebuild map and counts DataFrame
precinct_counts_df = pd.DataFrame(list(crime_counts.items()), columns=["NAME", "count"])

# Create map
choropleth_map = folium.Map(location=[39.4, -76.6], zoom_start=10)

# Add choropleth layer
Choropleth(
    geo_data=choropleth_geojson_path,
    data=precinct_counts_df,
    columns=["NAME", "count"],
    key_on="feature.properties.NAME",
    fill_color="YlOrRd",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Crime Count by Precinct (Sample)"
).add_to(choropleth_map)

# Save the map
choropleth_map_path = "/users/mobi/downloads/baltimore-county-crime-analysis/outputs/baltimore_choropleth_map.html"
choropleth_map.save(choropleth_map_path)

choropleth_map_path


'/users/mobi/downloads/baltimore-county-crime-analysis/outputs/baltimore_choropleth_map.html'

In [14]:
choropleth_map

In [17]:
import pandas as pd
import folium
from folium.plugins import TimestampedGeoJson
from shapely.geometry import Point

# Load crime data
crime_df = pd.read_csv("/users/mobi/downloads/Baltimore-county-crime-analysis/data/Public_Crime_Data.csv")

# Filter for valid coordinates and dates
crime_df = crime_df.dropna(subset=["OBF_YCOORD", "OBF_XCOORD", "OCCURREDON"]).copy()
crime_df["datetime"] = pd.to_datetime(crime_df["OCCURREDON"], errors='coerce')
crime_df = crime_df.dropna(subset=["datetime"])

# Sample to avoid browser lag (adjust size as needed)
crime_sample = crime_df.sample(n=1000, random_state=42)

# Convert to GeoJSON features with timestamps
features = []
for _, row in crime_sample.iterrows():
    feature = {
        "type": "Feature",
        "geometry": {
            "type": "Point",
            "coordinates": [row["OBF_XCOORD"], row["OBF_YCOORD"]],
        },
        "properties": {
            "time": row["datetime"].strftime("%Y-%m-%dT%H:%M:%S"),
            "popup": row["OFFENSE"]
        },
    }
    features.append(feature)

geojson = {
    "type": "FeatureCollection",
    "features": features
}

# Create folium map
m = folium.Map(location=[39.4, -76.6], zoom_start=10)

# Add timestamped GeoJSON
TimestampedGeoJson(
    geojson,
    transition_time=200,
    period="PT1H",
    add_last_point=True,
    auto_play=True,
    loop=False,
    max_speed=10,
    loop_button=True,
    date_options="YYYY-MM-DD HH:mm:ss",
    time_slider_drag_update=True,
).add_to(m)

# Save the animated map
m.save("/users/mobi/downloads/Baltimore-county-crime-animation.html")


/var/folders/b9/t16cvz9j5plbst_c7jrxgxl40000gn/T/ipykernel_74874/67118019.py:7: DtypeWarning: Columns (9) have mixed types. Specify dtype option on import or set low_memory=False.
  crime_df = pd.read_csv("/users/mobi/downloads/Baltimore-county-crime-analysis/data/Public_Crime_Data.csv")


In [19]:
m